## TP https://auder.net/miage/E_seance9-10_Classification/exos/TP_ensemble.pdf

In [150]:
# Some utils

library(rpart)
library(visNetwork)

splitData <- function(data, propTrain=0.7) {
  n <- nrow(data)
  indices <- sample(n, floor(propTrain * n))
  list(train=data[indices,], test=data[-indices,])
}

errorTree <- function(dataTrain, dataTest, variable, control=list()) {
  tree <- rpart(as.formula(paste(variable, "~ .")), data=dataTrain, method="class", control=control)
  predictions <- predict(tree, newdata=dataTest, type="class")
  err <- mean(predictions != dataTest[[variable]])
  list(err=err, tree=tree)
}

In [151]:
# 1] BAGGING

# Generic bagging: using any model obtained by "buildModel" function
bagging <- function(data, variable, buildModel, B=100, trace=FALSE) {
  if (trace) print("bagging")
  n <- nrow(data)
  modelList <- list()
  for (b in 1:B) {
    if (trace) print(paste("  Loop", b))
    indices <- sample(n, n, replace=TRUE)
    model <- buildModel(data[indices,], variable)
    modelList[[b]] <- model
  }
  modelList
}

# Call generic bagging function with model = tree
treeBagging <- function(data, variable, B=100, cp=0, trace=FALSE) {
  if (trace) print("treeBagging")
  buildModel <- function(data, variable) {
    rpart(as.formula(paste(variable, "~ .")), data=data, method="class", control=list(cp=cp))
  }
  bagging(data, variable, buildModel, B, trace)
}

# Predict by majority vote after B models have been trained
predictTreeBagging <- function(modelList, dataTest, trace=FALSE) {
  if (trace) print("predictTreeBagging")
  predictions <- sapply(modelList, predict, newdata=dataTest, type="class")
  predSummary <- apply(predictions, 1, table)
  unlist(lapply(predSummary, function(s) { sample(names(s[which.max(s)]), 1) }))
}

# Compare single tree error vs. bagging error
errorTreeBagging <- function(dataTrain, dataTest, variable, B=100, cp=0, trace=FALSE) {
  if (trace) print("errorTreeBagging")
  modelList <- treeBagging(dataTrain, variable, B, cp, trace)
  predictions <- predictTreeBagging(modelList, dataTest, trace)
  errBag <- mean(predictions != dataTest[[variable]])
  list(err=errBag, modlist=modelList)
}

In [152]:
# 2] BOOSTING

# Generic boosting: using any model obtained by "buildModel" function
# getErrPred() is supposed to return both error and predictions
boosting <- function(data, variable, buildModel, getErrPred, B=100, trace=FALSE) {
  if (trace) print("boosting")
  n <- nrow(data)
  K <- length(levels(data[[variable]]))
  modelList <- list()
  weights <- rep(1/n, n)
  sumModelWeights <- 0
  for (b in 1:B) {
    if (trace) print(paste("  Loop", b))
    indices <- sample(n, n, replace=TRUE)
    model <- buildModel(data[indices,], variable, weights[indices])
    e <- getErrPred(model, data, weights)
    if (e$error == 0 || e$error > 1 - 1/K) break
    alpha <- log((1 - e$error) / e$error) + log(K-1)
    sumModelWeights <- sumModelWeights + alpha
    modelList[[b]] <- list(model=model, weight=alpha)
    weights <- weights * exp(alpha * ifelse(e$predictions == data[[variable]], 0, 1))
    weights <- weights / sum(weights)
  }
  for (m in modelList) m$weight <- m$weight / sumModelWeights
  modelList
}

# Call generic boosting function with model = tree
treeBoosting <- function(data, variable, B=100, maxdepth=1, trace=FALSE) {
  if (trace) print("treeBoosting")
  buildModel <- function(data, variable, weights) {
    rpart(as.formula(paste(variable, "~ .")), data=data,
          method="class", weights=weights, control=list(maxdepth=maxdepth, cp=0))
  }
  getErrPred <- function(model, data, weights) {
    predictions <- predict(model, newdata=data, type="class")
    error <- sum(weights * ifelse(predictions != data[[variable]], 1, 0))
    list(error=error, predictions=predictions)
  }
  boosting(data, variable, buildModel, getErrPred, B, trace)
}

# Predict by weighted majority vote after B models have been trained
# prob: takes into account the (initial, individual) confidence of predictions.
predictTreeBoosting <- function(modelList, dataTest, prob=FALSE, trace=FALSE) {
  if (trace) print("predictTreeBoosting")
  getPredMat <- function(m) {
    p <- predict(m$model, newdata=dataTest, type="prob")
    if (prob) m$weight * p
    else {
      # Certainly not the most efficient (TODO...)
      res <- p + (1 - apply(p, 1, max))
      res[res != 1] <- 0
      m$weight * res
    }
  }
  predictions <- lapply(modelList, getPredMat)
  sumPred <- Reduce(`+`, predictions)
  colnames(sumPred)[apply(sumPred, 1, which.max)]
}

# Compare single tree error vs. boosting error
errorTreeBoosting <- function(dataTrain, dataTest, variable, B=100, maxdepth=1, prob=FALSE, trace=FALSE) {
  if (trace) print("compareErrorsBoosting")
  modelList <- treeBoosting(dataTrain, variable, B, maxdepth, trace)
  predictions <- predictTreeBoosting(modelList, dataTest, prob, trace)
  errBoo <- mean(predictions != dataTest[[variable]])
  list(err=errBoo, modlist=modelList)
}

Sur iris, le paramètre cp n'a pas d'influence car l'arbre non élagué n'a - en général - que trois feuilles. On obtient souvent la même erreur pour l'arbre seul et le bagging, autour de quelques pourcents.

In [153]:
d <- splitData(iris)
variable <- "Species"
errorTreeBagging(d$train, d$test, variable)$err
errorTreeBoosting(d$train, d$test, variable)$err
errorTreeBoosting(d$train, d$test, variable, maxdepth=2)$err

[1] 0.02222222

[1] 0.02222222

[1] 0.02222222

In [154]:
errTree <- errorTree(d$train, d$test, variable, list(cp=0))
errTree$err

[1] 0.06666667

In [155]:
visTree(errTree$tree)

HTML widgets cannot be represented in plain text (need html)

Sur un jeu de données plus complexe, où je sais qu'un arbre s'en sort raisonnablement :

In [156]:
adult <- read.table('https://archive.ics.uci.edu/ml/machine-learning-databases/adult/adult.data',
                    sep = ',', strip.white=T,
                    colClasses=c(NA,"factor",NA,"factor",NA,"factor","factor","factor","factor",
                                 "factor",NA,NA,NA,"factor","factor"))

Quelques bizarreries dans le fichier de test :

wget http://archive.ics.uci.edu/ml/machine-learning-databases/adult/adult.test  
sed -i "1 d; s/.$//g" adult.test

Réuploadé sur auder.net/miage :

In [157]:
adult.test <- read.table("https://auder.net/miage/E_seance9-10_Classification/data/adult.test",
                         sep = ',', strip.white=T, header=F,
                         colClasses=c(NA,"factor",NA,"factor",NA,"factor","factor","factor","factor",
                                      "factor",NA,NA,NA,"factor","factor"))

In [158]:
variable <- "V15"
d <- list(train=adult, test=adult.test)

In [159]:
errTree <- errorTree(d$train, d$test, variable, list(cp=0))
errTree$tree$cptable

CP           nsplit rel error xerror    xstd       
1  1.263869e-01   0    1.0000000 1.0000000 0.009839876
2  6.402245e-02   2    0.7472261 0.7472261 0.008840225
3  3.749522e-02   3    0.6832037 0.6832037 0.008532119
4  4.846321e-03   4    0.6457085 0.6457085 0.008339388
5  4.591251e-03  11    0.6013264 0.6091060 0.008141736
6  3.826043e-03  12    0.5967351 0.6060451 0.008124761
7  3.252136e-03  13    0.5929091 0.5981380 0.008080577
8  1.785487e-03  16    0.5816860 0.5862773 0.008013395
9  1.657952e-03  21    0.5712282 0.5821961 0.007990024
10 1.530417e-03  23    0.5679123 0.5786252 0.007969464
11 1.317859e-03  25    0.5648514 0.5787527 0.007970200
12 1.275348e-03  28    0.5608978 0.5802831 0.007979022
13 1.147813e-03  30    0.5583471 0.5788802 0.007970936
14 8.927433e-04  31    0.5571993 0.5792628 0.007973143
15 8.289759e-04  32    0.5563066 0.5796455 0.007975349
16 7.014411e-04  41    0.5478893 0.5810483 0.007983426
17 6.631807e-04  43    0.5464864 0.5795179 0.007974614
18 6.376738e-04  53    0.5380691 0.5797730 0.007976084
19 5.739064e-04  62    0.5316924 0.5770948 0.007960622
20 5.420227e-04  74    0.5240403 0.5741615 0.007943621
21 5.101390e-04  82    0.5197041 0.5741615 0.007943621
22 4.463716e-04  88    0.5166433 0.5725035 0.007933981
23 4.251158e-04  92    0.5148578 0.5733963 0.007939175
24 4.144879e-04  98    0.5123071 0.5730136 0.007936950
25 3.826043e-04 104    0.5095013 0.5730136 0.007936950
26 3.400927e-04 132    0.4982783 0.5763295 0.007956194
27 3.188369e-04 135    0.4972580 0.5788802 0.007970936
28 2.975811e-04 149    0.4919015 0.5786252 0.007969464
29 2.550695e-04 159    0.4887132 0.5880627 0.008023579
30 2.423160e-04 169    0.4861625 0.5939293 0.008056864
31 2.231858e-04 237    0.4600179 0.5975003 0.008076993
32 2.125579e-04 241    0.4591251 0.5969902 0.008074123
33 2.040556e-04 280    0.4482847 0.6037495 0.008111982
34 1.913021e-04 285    0.4472644 0.6051524 0.008119796
35 1.700463e-04 327    0.4371891 0.6089784 0.008141031
36 1.594184e-04 344    0.4342558 0.6121668 0.008158642
37 1.530417e-04 349    0.4333631 0.6128045 0.008162155
38 1.457540e-04 355    0.4323428 0.6128045 0.008162155
39 1.275348e-04 362    0.4313225 0.6241551 0.008224182
40 1.093155e-04 443    0.4203545 0.6284913 0.008247628
41 1.020278e-04 457    0.4188241 0.6302768 0.008257242
42 9.565106e-05 462    0.4183140 0.6314246 0.008263411
43 8.502317e-05 497    0.4147430 0.6361433 0.008288671
44 6.376738e-05 513    0.4130851 0.6392042 0.008304971
45 5.465775e-05 558    0.4101518 0.6501722 0.008362836
46 5.101390e-05 565    0.4097692 0.6524678 0.008374841
47 4.251158e-05 585    0.4086213 0.6539982 0.008382824
48 3.188369e-05 603    0.4078561 0.6554011 0.008390127
49 2.550695e-05 607    0.4077286 0.6573141 0.008400065
50 1.821925e-05 631    0.4070909 0.6592271 0.008409977
51 1.417053e-05 638    0.4069634 0.6605025 0.008416572
52 0.000000e+00 647    0.4068359 0.6606300 0.008417230

In [160]:
# Valeur de cp estimée via le tableau ci-dessus :
cpVal <- 4e-04
errTree <- errorTree(d$train, d$test, variable, list(cp=cpVal))
errTree$err

[1] 0.139672

In [161]:
visTree(errTree$tree)

HTML widgets cannot be represented in plain text (need html)

In [162]:
errorTreeBagging(d$train, d$test, variable, cp=cpVal)$err
# On vérifie que l'erreur diminue :

[1] 0.135004

In [164]:
errorTreeBoosting(d$train, d$test, variable)$err
# Sur des arbres très simples, résultats équivalents à ceux du meilleur arbre :

[1] 0.1434187

In [165]:
# Augmentation de maxdepth : pas d'amélioration observée
for (depth in seq(3,9,2))
  print(paste("Profondeur", depth, ":", errorTreeBoosting(d$train, d$test, variable, maxdepth=depth)$err))

[1] "Profondeur 3 0.183281125238007"
[1] "Profondeur 5 0.173392297770407"
[1] "Profondeur 7 0.18272833364044"
[1] "Profondeur 9 0.18586081935999"


Un autre exemple : reconnaissance de caractères (A à Z)

In [166]:
letters <- read.table(
    "https://archive.ics.uci.edu/ml/machine-learning-databases/letter-recognition/letter-recognition.data",
    sep = ',', header=F, fill = F, colClasses=c("factor", rep(NA, 16)))

In [167]:
d <- splitData(letters)
variable <- "V1"

In [168]:
errTree <- errorTree(d$train, d$test, variable, list(cp=0))
errTree$tree$cptable

CP           nsplit rel error xerror    xstd       
1  0.032226029   0     1.0000000 1.0048414 0.001649568
2  0.030463280   3     0.9033219 0.9173991 0.002866051
3  0.026813645   5     0.8423954 0.8451512 0.003453810
4  0.025175034   6     0.8155817 0.8183376 0.003621833
5  0.024504692   7     0.7904067 0.7843736 0.003804751
6  0.024430210   8     0.7659020 0.7661254 0.003890752
7  0.023610904   9     0.7414718 0.7507076 0.003957277
8  0.023089528  10     0.7178609 0.7305229 0.004036363
9  0.021525398  11     0.6947713 0.6997617 0.004140498
10 0.020706093  12     0.6732459 0.6826307 0.004190384
11 0.019179205  13     0.6525398 0.6570088 0.004254722
12 0.018992999  15     0.6141814 0.6346641 0.004301157
13 0.017279905  16     0.5951884 0.5976464 0.004359032
14 0.011097870  17     0.5779085 0.5786534 0.004379765
15 0.010650976  18     0.5668107 0.5700879 0.004387161
16 0.010055117  19     0.5561597 0.5599583 0.004394354
17 0.009608223  20     0.5461046 0.5476687 0.004400829
18 0.009533741  21     0.5364964 0.5409653 0.004403324
19 0.009310293  22     0.5269626 0.5305378 0.004405755
20 0.008639952  23     0.5176523 0.5194399 0.004406405
21 0.007224788  24     0.5090124 0.5122151 0.004405755
22 0.007075823  25     0.5017876 0.5040965 0.004404014
23 0.006926858  27     0.4876359 0.4953821 0.004400955
24 0.006256517  28     0.4807091 0.4859228 0.004396236
25 0.006182035  29     0.4744526 0.4789215 0.004391802
26 0.005772382  30     0.4682705 0.4733353 0.004387689
27 0.005139282  32     0.4567258 0.4649188 0.004380524
28 0.004766870  33     0.4515865 0.4588857 0.004374670
29 0.004468941  35     0.4420527 0.4518844 0.004367119
30 0.004022047  37     0.4331149 0.4457769 0.004359866
⋮  ⋮            ⋮      ⋮         ⋮         ⋮          
65 8.937882e-04 134    0.2624758 0.2865336 0.003934120
66 8.689607e-04 141    0.2562193 0.2813198 0.003911578
67 8.193058e-04 144    0.2536124 0.2787129 0.003900072
68 7.448235e-04 153    0.2462386 0.2678385 0.003850342
69 7.199960e-04 162    0.2395352 0.2595710 0.003810618
70 7.075823e-04 165    0.2373752 0.2589006 0.003807322
71 6.703411e-04 171    0.2325339 0.2565172 0.003795514
72 6.517205e-04 192    0.2184567 0.2460897 0.003742140
73 6.455137e-04 197    0.2151795 0.2460897 0.003742140
74 5.958588e-04 203    0.2113064 0.2413228 0.003716790
75 5.586176e-04 219    0.2017727 0.2311187 0.003660443
76 5.462039e-04 221    0.2006554 0.2311187 0.003660443
77 5.213764e-04 224    0.1990168 0.2294801 0.003651124
78 4.468941e-04 243    0.1891107 0.2224043 0.003609996
79 4.096529e-04 273    0.1757039 0.2192760 0.003591346
80 3.724117e-04 277    0.1740652 0.2116043 0.003544358
81 3.351706e-04 307    0.1628929 0.2099657 0.003534087
82 3.165500e-04 313    0.1608819 0.2044540 0.003498914
83 2.979294e-04 319    0.1585729 0.2044540 0.003498914
84 2.606882e-04 339    0.1526143 0.2034858 0.003492634
85 2.234470e-04 341    0.1520930 0.1996127 0.003467208
86 1.986196e-04 367    0.1462833 0.1996127 0.003467208
87 1.862059e-04 370    0.1456875 0.1996872 0.003467702
88 1.489647e-04 376    0.1445702 0.1996872 0.003467702
89 1.241372e-04 400    0.1409951 0.1980486 0.003456799
90 1.117235e-04 403    0.1406227 0.1978251 0.003455306
91 9.310293e-05 405    0.1403992 0.1977506 0.003454807
92 7.448235e-05 409    0.1400268 0.1977506 0.003454807
93 6.384201e-05 420    0.1392075 0.1976762 0.003454309
94 0.000000e+00 427    0.1387606 0.1979741 0.003456302

In [171]:
# Valeur de cp trouvée via le tableau ci-dessus, tout en bas :
cpVal <- 7e-05
errTree <- errorTree(d$train, d$test, variable, list(cp=cpVal))
errTree$err

[1] 0.1896667

In [172]:
visTree(errTree$tree)
# Bon l'arbre est trop grand, on n'y voit rien...

HTML widgets cannot be represented in plain text (need html)

In [173]:
errorTreeBagging(d$train, d$test, variable, cp=cpVal)$err
# L'erreur continue de diminuer :

[1] 0.106

In [175]:
errorTreeBoosting(d$train, d$test, variable)$err
# Très forte erreur, sans doute car les arbres sont trop simples pour 26 classes

[1] 0.7718333

In [176]:
# Augmentation de maxdepth : nette amélioration observée, jusqu'à dépasser le bagging
for (depth in seq(3,9,2))
  print(paste("Profondeur", depth, ":", errorTreeBoosting(d$train, d$test, variable, maxdepth=depth)$err))

[1] "Profondeur 3 : 0.578166666666667"
[1] "Profondeur 5 : 0.306833333333333"
[1] "Profondeur 7 : 0.164"
[1] "Profondeur 9 : 0.0845"
